$$\DeclareMathOperator*{\argmin}{arg\,min}$$
$$\DeclareMathOperator*{\argmax}{arg\,max}$$

# Reinforcement Learning by David Silver

## Intro
- RL borrows from many fields
  - Neuroscience: dopamine reward systems
  - Engineering: control
  - Psychology: conditioning
  - Math: operations research
  - Economics: game theory
- RL vs SL
  - Reward signal vs labels
  - Delayed feedback vs immediate feedback
  - Sequential data vs I.I.D data
  - Actions influencing subsequent data vs independence
- Rewards
  - All goals can be described as maximization of expected cumulative reward
  - There can be either intermediate or end-of-episode reward
  - If the goal is to be as fast as possible, appropriate reward mechanism is -1 per time step
  - **Poker**: no intermediate reward; end-of-episode net $$$
- Sequential decision making
  - Actions maximize total future reward
  - Actions have long term consequences
  - Sometimes, we forfeit immediate reward for future gain (depending on our discount factor)
- State
  - History $= [(O_1,A_1,R_1),...,(O_t,A_t,R_t)]$
  - State = info used to determine "what next?"
    - $S=f(H)$
    - Env state = environment's private representation of the world
    - Agent state = agent's internal representation
      - ${S^a}\subset{S^e}$
    - Markov state $=p(S_{t+1}|S_t)=p(S_{t+1}|S_{1},...,S_{t})$
- **Poker** is a POMDP
- RL agents can be based on:
  - Policy: the agent's behaviour function
  - Value function: $Q(s,a)$
  - Model: agent's representation of the environment
- Policy-based
  - Map from state to action
  - Deterministic $\pi(s)=a$ OR stochastic $\pi(a|s)=P(A=a|S=s)$
- Value-based
  - Value function predicts future reward, we evaluate states based on this
  - $V_{\pi}(s) = \mathbb{E}_{\pi}[\sum_{t=0}^{\infty}{\gamma^{t}R_t}|S_t=s]$
- Model-based
  - Model predicts the environment will do next
  - P predicts the next state
    - $P_{ss'}^{a} = p(S'=s'|S=s,A=a)$
  - R predicts the immediate reward
    - $R_{s}^{a} = E[R|S=s,A=a]$
- Model-free vs model-based
  - Free: works on policy and/or value function
  - Based: works on model + policy + value function
- Explore and exploit
  - Explore: give up reward to learn more about environment
  - Exploit: take good reward when it is known
    - Exploiting allows us to explore down more **optimal** paths

## Markov Decision Process
- MDP: formal definition for environment for RL
- ALmost all RL is MDPs
  - optimal control == continuous action MDP
  - MDPs can have 1 state
- State transition matrix P: Markov chain
  - $P_{ss'} = p(S_{t+1}=s'|s_t=s)$
    - $P = \begin{bmatrix}
        from(1)to(1) & from(1)to(2) \\
        from(2)to(1) & from(2)to(1)
        \end{bmatrix}$
- Markov reward process (MRP): Markov chain with values
  - $R_s = \mathbb{E}[R_{t+1}|S_t=s]$
  - $return = G_t = \sum_{k=0}^{\infty}\gamma^{k}R_{t+k+1}$
  - Why discount?
    - uncertainty about future rewards; dollar now > dollar tomorrow
    - the reward diverges to infinity if we don't discount
    - If all sequences terminate, discounting isn't necessary
- Bellman equation
  - Value function: $V(s) = \mathbb{E}[G_t|S_t=s]$
  - Bellman equation: $V(s) = \mathbb{E}[R_{t+1}+{\gamma}v(S_t)|S_t=s]$
  - $v = R + {\gamma}Pv$
  - $v = \begin{bmatrix} v(1) \\ \vdots \\ v(n) \end{bmatrix}$
  - $v = \begin{bmatrix} R(1) \\ \vdots \\ R(n) \end{bmatrix} + {\gamma} \begin{bmatrix} p_{11} & \cdots & p_{1n} \\ \vdots & \ddots & \vdots \\ p_{n1} & \cdots & p_{nn} \end{bmatrix} \begin{bmatrix} v(1) \\ \vdots \\ v(n) \end{bmatrix}$
  - Bellman solvable: $v = R+{\gamma}Pv = (I-{\gamma}P)^{-1}R$
    - Complexity is $O(n^3)$, so this is impractical
- MRP to MDP: from rewards to decisions
  - $(S,P,R,\gamma) \rightarrow (S,\textbf{A},P,R,\gamma)$
  - $P_{ss'}^{a} = p(S_{t+1}=s'|S=s_t, A=a$
  - $R_{s}^{a} = \mathbb{E}[R_{t+1}|S_t=s,A_t=a]$
    - sometimes, $(r|a)=r$, in that case:
    - $R_{s} = \mathbb{E}[R_{t+1}|S_t=s]$
  - MDP policy is time-independent, stationary
  - $V(s)_{\pi}$ is subbed by $\pi$ because the policy influences the value of the state; a good policy that is taking full advantage of the state will give it a larger value
  - $Q(s,a) = \mathbb{E}[G_t|S_t=s,A_t=a]$ = action value
  - For ANY MDP, $\exists \pi^{\star} \ge \pi \forall \pi$
- Extensions to MDP
  - Infinite and continuous MDPs
  - POMDP
  - Undiscounted, average reward MDP

## Planning by Dynamic Programming
- Breaking down the term
  - Dynamic -> sequential or temporal problem
  - Programming -> a policy, a mathematical program (not, like, a C program)
- Dynamic programming requires:
  - Optimal substructure
    - You can break down the problem into pieces, solve the pieces, and put them together to solve the main problem
  - Overlapping subproblems
    - The subproblems occur many times
    - we can cache the subproblem solutions and use them again and again
  - e.g. shortest path:
    - $sp(a_{0},a_{n}) = sp(a_{0},a_{1}) + sp(a_{1},a_{2}) + \cdots + sp(a_{n-1}, a_{n})$
- Does an MDP satisfy the requirements of DP?
  - The Bellman equation is the recursive decomposition that gives us optimal substructure; it's the immediate problem, plus the future problem
  - Value function stores and re-uses the subproblems; it's the cache
  - So yes. MDPs can be solved with DP using value iteration
- DP used for: prediction, control
  - Prediction
    - Input:
      - MDP $\langle S,A,P,R,\gamma \rangle$ and policy $\pi$, or
      - MRP $\langle S,P^{\pi}, R^{\pi}, \gamma \rangle$
    - Output:
      - Value function $V_{\pi}$
    - We want to predict the value of each state based on following the policy in the MDP
  - Control
    - Input:
      - MDP $\langle S,A,P,R,\gamma \rangle$
    - Output:
      - optimal value function $V_{\star}$
      - optimal policy $\pi_{\star}$ (implied from optimal value function)
    - We want to know what the best possible policy is for this MDP
- Policy evaluation
  - Problem: evaluate a given policy $\pi$
  - Solution: iterative application of Bellman expectation backup
    - $v_1 \rightarrow v_2 \rightarrow \cdots \rightarrow v_\pi$
    - Using synchronous backups, at each iteration $k+1$, for all states $s \in S$, update $v_{k+1}(s)$ from $v_{k}(s')$, where s' is a successor state of s
  - Full math:
    - $v_{k+1}(s) = \sum_{a \in A}{\pi(a|s)[R_{s}^{a} + \gamma \sum_{s' \in S}{P_{ss'}^{a}v_{k}(s')}]}$
    - Vector: $\textbf{v}^{k+1} = \textbf{R}^{\pi} + \gamma \textbf{P}^{\pi}\textbf{v}^{k}$
  - No math:
    - Compute the value for a state by looking at all possible actions, and taking the weighted sum of the values of the possible next states (weighted by probability of that stochastic action actually taking you to that state), plus the immediate reward of the action
- Policy iteration
  - Intuition:
    - Evaluate the policy $\pi$
      - $v_{\pi}(s) = \mathbb{E}[R_{t+1} + \gamma R_{t+2} + \cdots | S_t=s]$
    - Improve the policy by acting greedily w.r.t $\pi$
      - $\pi' = greedy(v_\pi)$
  - Formal:
    - Consider a deterministic policy $a=\pi(s)$
    - We improve the policy by acting greedily
      - $\pi'(s) = \argmax_{a \in A}{q_{\pi}(s,a)}$
    - This improves the value from any state s over one step:
      - $q_{\pi}(s, \pi'(s)) = \max\limits_{a \in A}q_\pi(s,a) \ge q_\pi(s,\pi(s)) = v_{\pi}(s)$
        - $q_{\pi}(s, \pi'(s))$: the value of following our new greedy policy for this one step, then following $\pi$ afterwards (max action, then $\pi$)
        - $v_{\pi}(s)$: the value of just following $\pi$ all the time (no max action now, just $\pi$ forever)
      - We can say that it's always at least as good because:
        - At all future states, they're the same policy
        - At this current state, the new one is the max; it's the best. The old one could only possibly be equal to it, but it can't be better
    - If improvements stop, then the Bellman optimality equation is satisfied, and therefore we've reached the optimal policy
      - $q_{\pi}(s, \pi'(s)) = \max\limits_{a \in A}q_\pi(s,a) = q_\pi(s,\pi(s)) = v_{\pi}(s)$
      - $v_{\pi}(s) = \max\limits_{a \in A}q_\pi(s,a)$
      - $v_{\pi}(s) = v_{\star}(s) \forall s \in S$
- Early stopping of policy evaluation
  - Does policy evaluation need to converge to $v_{\pi}$?
  - $\epsilon$-convergence of value function would work
    - if the value doesn't change by more than $\epsilon$, stop iterating
  - Stop evaluating after k iterations, enter policy iteration; loop around like this
  - Update policy every iteration, i.e. $k = 1$
    - This is exactly value iteration
- Value iteration
  - If we know the solution to subproblems $v_{\star}(s')$, then solution $v_{\star}(s)$ can be found by one-step lookahead
    - $v_{\star}(s) \leftarrow \max\limits_{a \in A}R^{a}_{s} + \gamma \sum_{s' \in S}P^{a}_{ss'}v_{\star}(s')$
  - We start by throwing some value in for $v(s')$ and saying it's optimal, even if it isn't; we back that value up to s, s becomes s', and we do this iteratively again and again until we converge to the actual value
- Value vs Policy iteration
  - Value iteration is policy iteration, but where we act on the policy after every step
  - Rather than update the value, update the policy, update the value based on the updated policy... we just jump from value function to value function

  | Problem    | Bellman Equation                                | Algorithm                   |
  |------------|-------------------------------------------------|-----------------------------|
  | Prediction | Bellman expectation                             | Iterative policy evaluation |
  | Control    | Bellman expectation + greedy policy improvement | Policy iteration            |
  | Control    | Bellman optimality                              | Value iteration             |

- Extensions to dynamic programming (asynchronous backups)
  - Back up states individually, in some order (what is the best order?)
  - In-place dynamic programming
    - Instead of storing $V_{old}$ and $V_{new}$, computing each $V_{new}(s)$ based on $V_{old}$, then replacing $V_{old} = V_{new}$...
    - Just update the state right away: $v(s) \leftarrow \max_{a \in A}(R_{s}^{a} + \gamma \sum_{s' \in S}p_{ss'}^{a}v(s'))$
    - Now every update is constantly using the most recent values, not the values from the last iteration; when we update state \#5, and then use it to compute state \#4, state 4 is getting the brand new value we just computed for state 5
  - Prioritized sweeping
    - Which state is the most important? The one that has the greatest change in value (Bellman Error)
      - $|\max_{a \in A}(R_{s}^{a}+ \gamma \sum_{s' \in S}P_{ss'}^{a}v(s')) - v(s)|$
    - Backup the state with the largest remaining Bellman error
    - Update Bellman error of affected states after each backup
    - Maintain this in a priority queue
  - Real-time dynamic programming
    - Let the agent interact and choose the states to update; where the agent is, that's where you update

## Model-Free Prediction
- This is used to estimate the value function of an unknown MDP
- Monte Carlo Learning
  - MC methods learn directly from episodes of experience (entire episodes, entire games)
  - MC is model-free; no knowledge of MDP transitions / rewards necessary
  - MC learns from *complete* episodes; no bootstrapping
  - Simplest possible value calculation: the mean reward over all episodes from that state
  - Can only be applied to episodic MDPs (must terminate)
  - Policy evaluation
    - We want to learn $v_{\pi}$ from episodes of experience of using $\pi$
    - We know that $v_{\pi}(s) = \mathbb{E}_{\pi}[R_{t+1} + \gamma R_{t+2} + \cdots + \gamma^{T-1}R_{T} | S_t = s]$
    - MC policy evaluation uses the mean of the returns it gets in place of the expectation
    - How do we do this for all states when we don't get to reset ourselves to each state a bunch of times?
      - First-visit MC policy evaluation
        - $S(s) = 0$, $N(s) = 0$
        - On first visit to s: $N(s) \leftarrow N(s) + 1$, $S(s) \leftarrow S(s) + G_t$
        - $V(s) = S(s)/N(s)$
        - Law of large numbers: as $N(s) \rightarrow \infty$, then $V(s) \rightarrow v_\pi(s)$
        - Basically, we're taking a mean over all episodes of the total discounted reward seen at the state at each episode
        - Since this is policy *evaluation*, we can assume that the policy we're evaluating is visiting the states it cares about
        - This exercise isn't about finding the best states, it's about getting a value function to approximate the value under the policy we're evaluating
      - Every-visit MC policy evaluation
        - Instead of only including the first visit, you include every visit
        - Increment every visit, add G every visit
    - Updating the MC value incrementally
      - Incremental mean calculation:
        - Calculating a mean doesn't have to happen all at once; it can happen incrementally
      ```
      u = 0
      nums = range(1,11)
      for i,n in enumerate(nums): u += 1/(i+1.) * (n-u)
      ```
      - Incremental MC updates
        - Update V(s) incrementally after each episode using this mean update
          - $N(S_t) \leftarrow N(S_t) + 1$
          - $V(S_t) \leftarrow V(S_t) + \frac{1}{N(S_t)}(G_t-V(S_t))$
        - In non-stationary problems, may want to forget old episodes
          - $V(S_t) \leftarrow V(S_t) + \alpha(G_t - V(S_t))$
          - Most problems are actually non-stationary, because it's w.r.t. the policy, which is improving
- Temporal difference learning
  - Learn directly from episodes; model-free
  - Learn from incomplete episodes by bootstrapping
    - Take what you have, estimate the remainder of the episode
  - TD(0)
    - Update $V(S_t)$ toward estimated return $R_{t+1}+\gamma V(S_{t+1})$
      - $V(S_t) \leftarrow V(S_t) + \alpha(R_{t+1}+\gamma V(S_{t+1}) - V(S_t))$
    - It learns before the final outcome, or even without the final outcome (non-terminating environments)
- MC vs TD
  - MC
    - High bias, zero variance
    - Good convergence
    - Not very sensitive to initial values
    - Does not exploit Markov property
  - TD
    - Some bias, low variance
    - TD(0) converges to $v_\pi(s)$
    - Usually more efficient than MC
    - More sensitive to initial values
    - Exploits Markov property
- Properties
  - Bootstrapping
    - Do we use the actual returns, or our own estimate of the returns?
    - MC = no bootstrapping (actual returns)
    - TD = bootstrapping (estimate returns)
  - Sampling
    - Do we sample a trajectory of the tree, or take an expectation over the whole tree?
    - MC = sampling
    - TD = sampling
    - DP = no sampling (requires full MDP knowledge)
  - Bootstrapping: how deep down the tree do we drill down?
  - Sampling: how wide across the tree do we drill down?
- TD(lambda)
  - TD(0) is the case where our bootstrapping is a 1 step lookahead; we take the value function one action in the future, and back that up to s
  - What if we went 2 steps ahead, and backed that up? Or 3 steps? Or 4? Or n? That's controlled by $\lambda$
  - We don't know what the best n is, so let's average over all of them
  - The proper way to average over all n (and still be able to compute it efficiently) is to use a gemoetric series that, while a sum, can be computed in closed form (so it's the same complexity as TD(0))
    - $G^{\lambda}_{t} = (1-\lambda)\sum_{n=1}^{\infty}\lambda^{n-1}G_{t}^{(n)}$
  - This form, called forward-view still requires, like MC, to be computed at the end of an episode (so that it has available all N-step returns)
- Backward view TD lambda
  - To use TD-lambda and still update online, every step, from incomplete sequences, we need a way around requiring all N steps
  - Eligibility traces
    - In credit assignment, we want to balance between the states that were most recent from the point of reward, and the states that were most frequent along the whole trip
      - $E_0(s)=0$
      - $E_t(s) = \gamma\lambda E_{t-1}(s) + I(S_t=s)$
      - Exponentially decay its eligibility over time t (first term), but spike it by 1 every time it shows up again
  - Keep an eligibility trace for every state s
  - Udate value V(s) for all states s in proportion to TD-error $\delta_t$ and eligibility trace $E_t(s)$:
    - $\delta_t = R_{t+1} + \gamma V(S_{t+1}) - V(S_t)$
    - $V(s) \leftarrow V(s) + \alpha \delta_t E_t(s)$
  - The states that we think are most responsible for the error get updated the most
  - $\lambda = 0$ means we only update the current state; this is TD(0)
  - $\lambda = 1$ means credit is deferred until the end of the episode; an episodic environment with offline updates
  - equivalent update to MC
- The sum of offline updates is identical for forward-view and backward-view
  - $\sum_{t=1}^{T}{\alpha \delta_t E_t(s)} = \sum_{t=1}^{T}\alpha(G_{t}^{\lambda} - V(S_t))I(S_t=s)$
  - If you're adding up all the rewards after everything has been seen, it doesn't matter if you go forward or backward

## Model-Free Control
- On-polcy vs off-policy learning
  - On: learn about $\pi$ from experience sampled from $\pi$
  - Off: learn about $\pi$ from experience sampled from $\mu$
    - off-policy is like if you show a robot how to vaccuum, and then give it a vaccuum; it learns from you
    - on-policy is like if you just hand a robot a vaccuum; it has to learn on its own
- Evaluation --> improvement --> evaluation --> improvement
  - Framework: iterative policy evaluation, greedy policy improvement
  - Can we plug in Monte Carlo evaluation here? Evaluate episodes by their mean reward --> act greedily --> evaluate episodes by mean reward? No.
    - This won't explore well at all, since we're acting greedily
    - It will take a long time, because we're getting episodic reward
    - Acting greedily requires finding V(s) which requires knowing the dynamics of the MDP (the transition model). We don't know that because we're model free, so we can't work with a value function
- Can we fix the greedy property?
  - Simplest (but most effective) fix: $\epsilon$-greedy exploration
    - $p(a^*) = \frac{\epsilon}{m} + 1 - \epsilon$
    - $p(a_{random}) = \frac{\epsilon}{m}$
    - this always results in a policy that is $\ge$ the previous policy
- Monte Carlo evaluation + $\epsilon$-greedy improvement; how can we improve it?
  - Instead of doing policy evaluation to convergence, we can just estimate it by doing one episode at a time
    - One episode of evaluation, then improve; one episode of evaluation, then improve, etc.
- Greedy in the limit with infinite exploration
  - Two properties should be satisfied by our exploration technique:
    - $\lim_{k\rightarrow\infty}\pi_k(a|s) = N_k(s,a) = \infty$; it sees each state infinitely many times
    - $lim_{k\rightarrow\infty}\pi_k(a|s) = 1(a = \argmax_{a'\in A}Q_k(s,a'))$ it converges on the greedy policy
- GLIE with Monte Carlo control algorithm
  - Sample an episode according to $\pi$
  - For each state/action pair in the episode:
    - $N(S_t,A_t) \leftarrow N(S_t,A_t)+1$
    - $Q(S_t,A_t) \leftarrow Q(S_t,A_t) + \frac{1}{N(S_t,A_t)}(G_t-Q(S_t,A_t))$
  - Improve policy based on new action-value function Q
    - $\epsilon \leftarrow 1/k$
    - $\pi \leftarrow greedy_\epsilon(Q)$
  - This converges to the optimal Q*, but it's horribly inefficient; we need to replace Monte Carlo with TD
- Replace MC with TD
  - TD is lower variance, it's online, and it works with incomplete sequences
  - Apply TD to Q(s,a), use $\epsilon$-greedy policy improvement still, update every time step
- SARSA (state/action -> reward -> next state / next action)
  - $Q(S,A) \leftarrow Q(S,A) + \alpha(R+\gamma Q(S',A') - Q(S,A))$
  - Every time step, we evaluate the policy, and act epsilon-greedily
- Forward and backward view SARSA
  - $Q(S_t,A_t) \leftarrow Q(S_t,A_t) + \alpha(q_t^\lambda - Q(S_t,A_t))$
  - $q_t^\lambda = (1-\lambda)\sum_{n=1}^{\infty}\lambda^{n-1}q_t^{(n)}$
  - Backward view: replace $q_t^\lambda$ with eligibility trace as before with prediction (eligiblity traces are 1 per state/action pair)
- Off-policy learning
  - evaluate target policy while following different behaviour policy
  - Why?
    - Learn from observing other humans/agents
    - re-use experience from previous policies
    - learn about optimal policy while following exploratory policy
    - learn about multiple policies while following one policy
  - Q learning is an off-policy algorithm
    - we choose actions according to an epsilon-greedy (exploratory) policy, but we update our Q values with future Q values that are assuming the optimal policy


## Value Function Approximation
- Large / continuous state spaces are impossible to store in a table
  - We instead approximate a function mapping from state to value
    - $v(s,\textbf{w}) \approx v_\pi(s)$
    - $q(s,a,\textbf{w}) \approx q_\pi(s,a)$
  - Instead of updating state values, we update the parameters of this function (with MC or TD)
  - 3 ways to approach it:
    - from s to v(s)
    - from s,a to q(s,a)
    - from s to q(s,a1) ... q(s,aN)
  - Linear function approximation or non-linear using NNs (differentiable a requirement)
- We optimize w by stochastic gradient descent, just like with NNs
  - value function is represented by a linear combination of the features of the state
  - for linear, the objective function is quadratic, so convex, so global minimum is attainable
  - its gradient is very simple:
    - if $v(S,\textbf{w}) = x(S)^T\textbf{w}$, then $\nabla_\textbf{w}{v(S,\textbf{w})} = x(S)$
  - then update = step_size * prediction_error * feature_value
    - $\nabla{\textbf{w}} = \alpha(v_\pi(S) - v(S,\textbf{w}))\textbf{x}(S)$
- Table lookup is a special case of linear function approximation
  - $x(S) = \begin{pmatrix} I(S=s_1) \\ \vdots \\ I(S=s_n) \end{pmatrix}$
  - $v(S,\textbf{w}) = \begin{pmatrix} I(S=s_1) \\ \vdots \\ I(S=s_n) \end{pmatrix} \cdot \begin{pmatrix} w_1 \\ \vdots \\ w_n  \end{pmatrix}$
  - In this case we're just picking out the weight that corresponds to the state and updating only that
- We need to approximate $v_\pi(S)$, because we don't actually have it
  - MC: total return $G_t$
  - TD(0): $R_{t+1} + \gamma v(S_{t+1},\textbf{w})$
  - TD($\lambda$): discounted return $G_t^\lambda$
- Convergence
  - MC converges whether linear or non-linear
  - Linear TD(0) converges close to the global optimum, but the rest don't
  - TD($\lambda$) is more difficult to get to converge, because it's not following the actual gradient (we just plugged in G and hoped it was close to V); Gradient TD converges
- State/action value functions q are the same idea
  - our feature vector can now include features extracted from both the state and the actions (e.g. stack size if bet 50)
- Batch methods use the data more efficiently by applying gradient descent over batches and replaying the batches over and over to convergence
- Deep-Q Networks, the Atari method
  - DQN = Q learning + experience replay + fixed-Q targets
  - Q learning: the loss that the weight's gradient is pointed at is the error between the current Q and the (reward + max_future_Q)
  - experience replay: compute the gradient with respect to some minibatch of samples, rather than the whole memory or just the last sample
  - fixed Q: freeze a "past Q" to compute the error against, for maybe 1000 time steps; this is better than always using the last Q, because that moving target causes divergence
- SGD is least squares, which means for linear approximation it has a closed form solution, but with many state features the computation is inefficient because it's a matrix inversion which is O(n^3)

## Policy Gradient Methods
- From value function based to policy based
    - $V_\theta(s) \approx V^\pi(s)$ and $Q_\theta(s,a) \approx Q^\pi(s,a)$ become
    - $\pi_\theta(s,a) = P[a|s,\theta]$
    - No value function needed for policy-based
    - Actor-critic combines learning a value function and learning a policy
- Pros and cons of policy-based
    - Better convergence , effective in continuous action spaces (no max), and can learn stochastic policies (poker)
    - Typically converges to a local optimum, and evaluation is inefficient and high variance
    - Stochastic policies are great for games, and great in situations where our features don't fully distinguish different states (they would end up with the same policy, and they may not warrant the same policy)
- Policy objective functions: given a policy $\pi_\theta(s,a)$, find the best $\theta$; how do we evaluate which is the "best"?
    - Start value (episodic environments given a start state): $J_1(\theta) = V^{\pi_\theta}(s_1) = \mathbb{E}_{\pi_\theta}[v_1]$
    - Average value (continuing environments): $J_{avV}(\theta) = \sum_s d^{\pi_\theta}(s)V^{\pi_\theta}(s)$ (where d is the probability of getting to that state, a stationary distribution)
    - Average reward per time step: $J_{avR}(\theta) = \sum_s d^{\pi_\theta}(s) \sum_a \pi_\theta(s,a)R^a_s$
- Policy-based RL is an optimization problem
    - Genetic algorithms, simulated annealing, hill climbing, gradient descent, all possible tools for policy evaluation
- Finite differences for computing / evaluating gradients
    - For each dimension, estimate the partial by moving a bit in that direction and taking the slope
    - Must be done n times for n dimensions, on every evaluation
    - Wildly inefficient and noisy, but for some reason it works sometimes
- If we compute the gradient analytically, what is the score function?
    - Assume we know the gradient (because we designed the cost function), so we have $\nabla_\theta \pi_\theta(s,a)$
    - Use likelihood ratios:
        - $\nabla_\theta \pi_\theta(s,a) = \pi_\theta(s,a) \frac{\nabla_\theta \pi_\theta(s,a)}{\pi_\theta(s,a)}$
        - $\nabla_\theta \pi_\theta(s,a) = \pi_\theta(s,a)\nabla_\theta\log \pi_\theta(s,a)$
    - Score function: softmax policy
        - weight actions using a linear combination of features: $\phi(s,a)^T\theta$ ($\phi$ gives the feature vector)
        - probability of action is proportional to exponentiated weight: $\pi_\theta(s,a) \propto e^{\phi(s,a)^T\theta}$
        - score function is: $\nabla_\theta\log\pi_\theta(s,a) = \phi(s,a) - \mathbb{E}_{\pi_\theta}[\phi(s,\cdot)]$
        - so the score function is just, "how far away are these features from typical?"
    - Score function: Gaussian policy (for continuous action spaces)
        - The mean of the Gaussian is the linear combination of features: $\mu(s) = \phi(s)^T\theta$
        - Variance can be a fixed $\sigma^2$ or can be parameterized
        - Policy draws actions from a Gaussian
        - Score function: $\nabla_\theta\log_{\pi_\theta}(s,a) = \frac{(a-\mu(s))\phi(s)}{\sigma^2}$
        - score function is again, "how much more is this action happening than normal?"
- Policy gradients for one-step MDP
    - Start in state s, take one step, get one reward, done
    - Compute the policy gradient with likelihood ratios
        - $J(\theta) = \mathbb{E}_{\pi_\theta}[r]$
        - $J(\theta) = \sum_{s \in S}d(s)\sum_{a \in A}\pi_\theta(s,a)R_{s,a}$
            - The cost is, over all states, the expected reward over actions
        - $\nabla_\theta J(\theta) = \sum_{s \in S}d(s)\sum_{a \in A}\pi_\theta(s,a)\nabla_\theta\log\pi_\theta(s,a)R_{s,a}$
        - $\nabla_\theta J(\theta) = \mathbb{E}_{\pi_\theta}[\nabla_\theta\log\pi_\theta(s,a)r]$
            - The gradient is, in expectation over all states, the gradient of the log policy (which we simplified above) by the reward; it's score*reward
- Generalize to any MDP (policy gradient theorem)
    - Replace r with Q(s,a)
    - $\nabla_\theta J(\theta) = \mathbb{E}_{\pi_\theta}[\nabla_\theta\log\pi_\theta(s,a)Q^{\pi_\theta}(s,a)]$
- MC policy gradient
    - update parameters by stochastic gradient ascent using the policy gradient theorem, with return $v_t$ as an unbiased sample of $Q^{\pi_\theta}(s_t,a_t)$
    - $\nabla\theta_t = \alpha\nabla_\theta\log\pi_\theta(s_t,a_t)v_t$
    - algorithm
        - initialize $\theta$
        - for each episode:
            - for t in range(T):
                - $\theta \leftarrow \theta + \alpha\nabla_\theta\log\pi_\theta(s_t,a_t)v_t$
    - $v_t$ is the return, an estimate of Q
    - MC policy gradient is very slow and high variance, but it's a good idea in general
- Actor-critic policy gradient
    - To reduce variance, we estimate Q with another network / function approximator: $Q_w(s,a) \approx Q^{\pi_\theta}(s,a)$
    - We maintain these two networks:
        - Critic: updates action-value function (Q) parameters (w)
        - Actor: updates policy parameters $\theta$, in direction suggested by critic
    - Actor-critic follows an approximate policy gradient
        - $\nabla_\theta J(\theta) \approx \mathbb{E}_{\pi_\theta}[\nabla_\theta\log\pi_\theta(s,a) Q_w(s,a)]$
        - $\Delta\theta = \alpha\nabla_\theta\log\pi_\theta(s,a)Q_w(s,a)$
    - The critic's job of policy evaluation has been discussed in previous sections
- Actor-critic can be high variance, so to counter that, we subtract a baseline
    - If we subtract $V^{\pi_\theta}(s)$, it can be stable; the expectation doesn't change, but the variance is reduced
    - $A^{\pi_\theta}(s,a) = Q^{\pi_\theta}(s,a) - V^{\pi_\theta}(s)$
    - A is "how much better is this action in this state than the state in general? Does this action make the state better?
    - $\nabla_\theta J(\theta) = \mathbb{E}_{\pi_\theta}[\nabla_\theta\log\pi_\theta(s,a)A^{\pi_\theta}(s,a)]$
    - how do we estimate the advantage function? we don't have access to V(s)
    - observe that A is really just an expectation of the TD error
        - TD error: $\delta^{\pi_\theta} = r + \gamma V^{\pi_\theta}(s') - V^{\pi_\theta}(s)$
        - $\mathbb{E}_{\pi_\theta}[\delta^{\pi_\theta}|s,a] = \mathbb{E}_{\pi_\theta}[r + \gamma V^{\pi_\theta}(s') | s,a] - V^{\pi_\theta}(s)$
        - $\mathbb{E}_{\pi_\theta}[\delta^{\pi_\theta}|s,a] = Q^{\pi_\theta}(s,a) - V^{\pi_\theta}(s)$
        - $\mathbb{E}_{\pi_\theta}[\delta^{\pi_\theta}|s,a] = A^{\pi_\theta}(s,a)$
    - and plug that into the gradient
        - $\nabla_\theta J(\theta) = \mathbb{E}_{\pi_\theta}[\nabla_\theta\log\pi_\theta(s,a)\delta^{\pi_\theta}]$
- Actor-critic with eligiblity traces and TD(lambda)
    - $\Delta\theta = \alpha(v_t^\lambda - V_v(s_t))\nabla_\theta\log\pi_\theta(s_t,a_t)$
    - $\delta = r_{t+1} + \gamma V_v(s_{t+1}) - V_v(s_t)$
    - $e_{t+1} = \lambda e_t + \nabla_\theta\log\pi_\theta(s,a)$
    - $\Delta\theta = \alpha\delta e_t$

## Integrating Learning and Planning
- Learn a model directly from experience; plan with that model to construct a value function or policy
    - Model predicts: transition probabilities P, reward function R
    - Use the model to simulate the environment and generate experience without actually interacting with the world
    - It's still online; we use the active experience to build the model, and solve with the model (with e.g. tree search)
- Advantages and disadvantages
    - Good: In games with sharp value functions where a small change in state is a big change in reward, we can model that instead of learning with huge gradients
    - Good: We can efficiently learn the model with supervised learning methods
    - Good: We can reason about model uncertainty (offer Bayesian approaches to action selection)
    - Bad: We now have two layers of uncertainity; a noisy model of the world, and a noisy value function
- Model architecture
    - Learner 1: input $\{(s_i,a_i)\}_{i=1}^n$, output $\{r_i\}_{i=1}^n$ (regression problem)
    - Learner 2: input $\{(s_i,a_i)\}_{i=1}^n$, output $\{s_{i+1}\}_{i=1}^n$ (density estimation problem)
    - Example cost functions: RMSE for regression, KL Divergence for density estimation
- Toy example model, a table lookup
    - Could take mean of rewards from s,a as model reward for s,a; take count of s' from s,a as probability of s' from s,a
    - Could sample from experience tuples for s,a to get an s'; memory inefficient
- Sample-based planning
    - Use our model to generate sample experience (s,a,r,s')
    - Apply model-free RL e.g. Q-learning to sample experience
    - This gives us a source of infinite data that we can learn over for as long as we want
    - Our agent will only perform as well as our model of the environment
- Combining real and sampled experience
    - Dyna is an architecture for:
        - learning a model from real experience
        - learning and planning with a value function / policy from combined real and simulated experience
    - Dyna algorithm:
        - Initialize Q(s,a) and model(s,a)
        - while True:
            - pick and execute action epsilon-greedily
            - $Q(s,a) \leftarrow Q(s,a) + \alpha[R + \gamma\max_A{Q(s',A)} - Q(s,a)]$
            - $model(s,a) \leftarrow r,s'$
            - for i in range(N):
                - S <- random previously observed state
                - A <- random previously taken action from S
                - R,S' from model(S,A)
                - $Q(S,A) \leftarrow Q(S,A) + \alpha[R + \gamma\max_a{Q(S',a)} - Q(S,A)]$
    - Dyna idea: update Q with real experience, use updated Q to generate fake experience, continue to update Q with that experience
    - Efficient re-use of data to learn faster over the same amount of real experience
    - The more times we hallucinate data (the larger N is), the faster we will converge on the optimal value function / policy
- Dyna Q+
    - The + is a way of incentivizing exploration, in case the environment changes and we're still stuck on our policy
    - Say you're playing poker and suddenly a whole new table of players sits down; if you're not incentivized to explore, you'll just act according to your previously-optimal policy for a long time before figuring out that it sucks
- Forward search algorithms for simulation-based search
    - Forward search chooses the best action by lookahead
    - Build a search tree rooted at the current state (don't care about the past or about far off states)
    - Use our model (approximation to the MDP) to roll forward the dynamics and do lookahead
    - Solve the sub-MDP starting from the current state
- Forward search with sample-based planning
    - Generate samples using the dynamics to roll-forward episodes
    - Use those samples in a model-free setting and learn over those
- Simple MC search
    - Given a model and a simulation policy $\pi$ (doesn't have to be a great policy, but we will improve it)
    - For each action a in A:
        - simulate K episodes from current state, evaluate by mean return
    - Select best A from simulated mean return
- Monte Carlo Tree Search
    - Given a model
    - Simulate K episodes from current state
    - Build a search tree containing visited states and actions (tree that has state nodes and action nodes mapped out)
    - Evaluate states by mean return of episodes starting with s,a
    - Select best A based on maximum return from search tree
- MCTS simulation policy
    - $\pi$ improves because we're always (epsilon) maximizing over Q, always going down the best path and exploring the best parts of the tree
    - When we get to unexplored areas down the tree (further in the simulation) where they're all still at their initial, equivalent values, we pick actions randomly
- Replacing MC with TD
    - apply SARSA to sub-MDP from current state, instead of mean return
    - as always, TD is usually more efficient; it reduces variance, but increases bias
- Dyna-2; long + short term memory
    - long-term is updated with TD-learning over real experience
    - short-term is updated with TD-search over simulated experience from current state
    - value function is just the sum of the two value functions

## Exploration and Exploitation
- Are there better ways than epsilon-greedy to explore effectively?
    - Random exploration (this is epsilon-greedy)
    - Optimism in the face of uncertainty
        - Estimate uncertainty on value
        - Prefer to explore states/actions with the highest uncertainty (Dyna+)
        - State A is always +10, State B could be 5-20; try B. If it's better it's better, if not whatever
    - Information state space
        - Consider agent's information as part of its state
        - State variable is # of times we've been in this state
- State-action vs parameter exploration
    - State-action: systematically explore state-space and action-space; e.g. pick new A each time S is visited
    - Parameter: parameterize policy, randomly start fiddling with the parameters to try some new combination out
        - Advantage: exploration is consistent, not random; we change our parameters a bit so we're still kind of following the same path, but still kind of exploring
        - Disadvantage: doesn't know about state-action space (doesn't know what we've already tried)
- Example problem: multi-arm bandits
    - No states, just rewards and actions
    - Each bandit is an arm we can pull (action we can take) for some reward. We want to maximize our reward over many pulls
    - One step episodes
- Cost function for actions: regret
    - $L_t = \mathbb{E}[\sum_{\tau=1}^t v_\star - q(A_\tau)]$
    - The expected total difference over all actions between the optimal value and what we're actually getting
    - The "gap" for an action $\Delta_a$ is $\Delta_a = v_\star- q(a)$; the difference between that action and the best action
    - The "count" for an action is the expected number of uses of that action
    - Regret is a function of gaps and counts: $L_t = \sum_{a \in A}\mathbb{E}[N_t(a)]\Delta_a$
    - Optimizing regret thus means causing small counts for large gaps
- If we never explore, our regret will be huge, because we'll lock onto a sub-optimal action and incur regret forever
    - Exploration technique: optimistic initialization
        - Initialize every Q value to be the max reward possible
        - Everything is 100; we pull A, it gets 10, now everything but A is the best possible; we're guaranteed to try everything at least once, before deciding it sucks
    - Exploration technique: decaying epsilon for epsilon-greedy
        - pretend we know $v_\star$, the optimal value, and therefore know $\Delta_a$
        - pick this decaying schedule: $\epsilon_t = \min(1, \frac{c|A|}{d^2t})$, where $d = \min_{a|\Delta_a>0}\Delta_a$
        - this schedule guarantees logarithmic asymptotic total regret (it flatlines out to infinity instead of growing forever
- How can we replicate this decayed epsilon when we don't know $\Delta_a$, which we never do?
    - Use upper confidence bounds on each of the actions
    - with high probability, $q(a) \le Q_t(a) + U_t(a)$; thus, $U_t(a)$ acts as a sort of 95% confidence interval on the mean reward
    - U is inversely proportional to N; the more times we pick an action, the smaller it gets
- How do we set U?
    - Pick some probability p for our "confidence interval" (e.g. 5%); this is the probability that the true value exceeds the upper confidence bound
    - Hoeffding's inequality: $P[\mathbb{E}[X] > \overline{X}_t + u] \le e^{-2tu^2}$
    - $P[q(a) > Q_t(a) + U_t(a)] \le e^{-2N_t(a)U_t(a)^2}$
    - $U_t(a) = \sqrt{\frac{-\log{p}}{2N_t(a)}}$
    - Reduce p as we observe more rewards, e.g. $p = t^{-4}$ (be more confident that we're right as we experience)
- UCB1 algorithm
    - $A_t = \argmax_{a \in A}Q_t(a) + \sqrt{\frac{2\log t}{N_t(a)}}$
    - This will achieve the logarithmic asymptotic reward we wanted
- Bayesian approach when assuming / given prior distribution for actions
    - Bayesian UCB
        - $p[Q|w]$, we find a distribution for the action-value function (the reward) and parameterize it by w, which could be e.g. a vector of the means and variances of all the arms
        - use Bayes theroem to update the means and SDs, then pick a t-score and evaluate the actions at that t value (e.g. mean + 3 SDs, max a for that)
    - Bayesian probability matching with Thompson sampling
        - $\pi(a) = \mathbb{E}[1(Q(a) = \max_{a'}Q(a')) | R_1,...,R_{t-1}]$
        - Now we want to find the probability that each action is the best action
        - We just sample one reward from each action's distribution, and take the best action from those samples
        - This simple idea achieves the lower bound, and there are no hyperparameters like SD
- Information state exploration
    - Treat the reward distributions for actions as states, generate an MDP from that
    - The actions of the MDP are still the actions, and each child is an outcome from that action
        - If we do action A and it succeeds, that's a state; if we do action A and it fails, that's a state
    - If we use a beta distribution for each action, that's parameterized very easily by the counts of successes and failures (rewards of 0 and 1)
    - This is intractable without sampling and tree search (because we just exploded our state space size)
- How do we apply all of this to MDPs with states?
    - We just do it. This all generalizes when we add in s
    - e.g. $A_t = \argmax_{a \in A}Q(S_t,a) + U(S_t,a)$
    - One thing it doesn't account for is that our Q improves; U doesn't know how close Q is to the optimal policy, so it might still be suggesting to explore when we're almost done
    - Rmax algorithm
        - For any state we don't know about, set it to $R_max$; this will cause the MDP to guide us to that state, so that we can figure out its true value, then we do that again with another state
        - The MDP systematically guides us to each state